# Time series prediction:


#### This module predicts price of next hour based on last hour prices and previous day polarity using CNN.



In [2]:
import glob
import pandas as pd
import numpy as np
import requests
#import html5lib
from bs4 import BeautifulSoup
import datetime
import re


tweets_path = 'Tweets/bitcoin/'
crypto_name = 'bitcoin' 
dates=[]

## 1.Average Polarity per day

In [3]:
cols = ['date','polarity']
lst = []
df1 = pd.DataFrame(lst, columns=cols)
lst_dict = []
time_pol={}  # dict of date and polarity.

for f in glob.glob( str(tweets_path) + crypto_name + '*.txt'): # f is file name.

    df_datawise = pd.read_csv(f, sep='\t', encoding='utf-8', parse_dates=True)
    polarity = 0.00

    ct=0;
    for idx,row in df_datawise.iterrows():
        polarity += float(row["polarity"])
        dt=row["date"]
        ct=ct+1
    avg_pol=float(polarity/ct)
    lst_dict.append({'date':dt, 'polarity':avg_pol,})
    time_pol[dt]=avg_pol

            
df4 = df1.append(lst_dict) # avg polarity dataframe


In [4]:
df_price=pd.read_csv("bitcoin.csv", encoding='utf-8', parse_dates=True)


In [5]:
df_price['Timestamp'].size

525600

In [6]:
cols = ['Timestamp','Close']
lst = []
df_price1 = pd.DataFrame(lst, columns=cols)
lst_dict1 = []

In [7]:
df_price['Timestamp']=pd.to_datetime(df_price['Timestamp'])
for idx,r in df_price.iterrows():
    dt = r["Timestamp"].strftime("%Y-%m-%d")
#     print(time)
#     if(dt=="2017-02-11"):
#         print(dt)
    if dt in time_pol.keys():
        lst_dict1.append({'Timestamp':r['Timestamp'], 'Close':r['Close'],})
#         print(dt)
df_price_new = df_price1.append(lst_dict1)  #dataframe of 91 days

In [8]:
df_price_new

Timestamp    Close
0      2017-09-01 00:00:00  4740.00
1      2017-09-01 00:01:00  4740.00
2      2017-09-01 00:02:00  4739.90
3      2017-09-01 00:03:00  4738.59
4      2017-09-01 00:04:00  4736.09
...                    ...      ...
131035 2017-11-30 23:55:00  9800.01
131036 2017-11-30 23:56:00  9775.99
131037 2017-11-30 23:57:00  9751.06
131038 2017-11-30 23:58:00  9769.99
131039 2017-11-30 23:59:00  9770.00

[131040 rows x 2 columns]

In [9]:
price_arr=df_price_new.to_numpy()

In [10]:
price_arr.shape

(131040, 2)

### 2.Creating data frame for model:
each row have previous day polarity , closing price for 60 previous minutes and closing price of 61th minute.

In [11]:
price_arr[3,1]

4738.59

In [12]:
cols = ['Timestamp','polarity']
lst = []
df_price_final = pd.DataFrame(lst, columns=cols)
lst_dict2 = []

for i in range(1,62):
    cols.append(str(i))
    



for i in range(price_arr.shape[0]):
#     print(price_arr[i,0])
    dt = price_arr[i,0].strftime("%Y-%m-%d")
    polarity=time_pol[dt]
    dict_63={}
    
    if i+60<price_arr.shape[0]:
        dict_63['Timestamp']=price_arr[i+60,0]
        dict_63['polarity']=polarity
        
        for j in range(61):
            dict_63[str(j+1)]=price_arr[i+j,1]
        lst_dict2.append(dict_63)
        
df_final=df_price_final.append(lst_dict2)

In [13]:
df_final

Timestamp  polarity        1        2        3        4  \
0      2017-09-01 01:00:00  0.095204  4740.00  4740.00  4739.90  4738.59   
1      2017-09-01 01:01:00  0.095204  4740.00  4739.90  4738.59  4736.09   
2      2017-09-01 01:02:00  0.095204  4739.90  4738.59  4736.09  4735.10   
3      2017-09-01 01:03:00  0.095204  4738.59  4736.09  4735.10  4736.08   
4      2017-09-01 01:04:00  0.095204  4736.09  4735.10  4736.08  4736.09   
...                    ...       ...      ...      ...      ...      ...   
130975 2017-11-30 23:55:00  0.094750  9406.41  9417.48  9474.99  9473.00   
130976 2017-11-30 23:56:00  0.094750  9417.48  9474.99  9473.00  9473.00   
130977 2017-11-30 23:57:00  0.094750  9474.99  9473.00  9473.00  9473.00   
130978 2017-11-30 23:58:00  0.094750  9473.00  9473.00  9473.00  9472.00   
130979 2017-11-30 23:59:00  0.094750  9473.00  9473.00  9472.00  9484.00   

              5        6        7        8  ...       52       53       54  \
0       4736.09  4735.10  4736.08  4736.09  ...  4734.97  4735.49  4737.35   
1       4735.10  4736.08  4736.09  4739.86  ...  4735.49  4737.35  4737.35   
2       4736.08  4736.09  4739.86  4739.88  ...  4737.35  4737.35  4739.79   
3       4736.09  4739.86  4739.88  4739.89  ...  4737.35  4739.79  4742.95   
4       4739.86  4739.88  4739.89  4739.90  ...  4739.79  4742.95  4742.83   
...         ...      ...      ...      ...  ...      ...      ...      ...   
130975  9473.00  9473.00  9472.00  9484.00  ...  9800.00  9846.00  9799.00   
130976  9473.00  9472.00  9484.00  9488.00  ...  9846.00  9799.00  9808.28   
130977  9472.00  9484.00  9488.00  9487.95  ...  9799.00  9808.28  9800.01   
130978  9484.00  9488.00  9487.95  9488.99  ...  9808.28  9800.01  9814.97   
130979  9488.00  9487.95  9488.99  9490.00  ...  9800.01  9814.97  9816.00   

             55       56       57       58       59       60       61  
0       4737.35  4739.79  4742.95  4742.83  4742.79  4742.79  4742.79  
1       4739.79  4742.95  4742.83  4742.79  4742.79  4742.79  4742.79  
2       4742.95  4742.83  4742.79  4742.79  4742.79  4742.79  4734.01  
3       4742.83  4742.79  4742.79  4742.79  4742.79  4734.01  4726.96  
4       4742.79  4742.79  4742.79  4742.79  4734.01  4726.96  4727.39  
...         ...      ...      ...      ...      ...      ...      ...  
130975  9808.28  9800.01  9814.97  9816.00  9820.00  9808.00  9800.01  
130976  9800.01  9814.97  9816.00  9820.00  9808.00  9800.01  9775.99  
130977  9814.97  9816.00  9820.00  9808.00  9800.01  9775.99  9751.06  
130978  9816.00  9820.00  9808.00  9800.01  9775.99  9751.06  9769.99  
130979  9820.00  9808.00  9800.01  9775.99  9751.06  9769.99  9770.00  

[130980 rows x 63 columns]

In [14]:
df_final.to_csv(r'time_frame.csv')

In [15]:
df_final1=df_final
df_final1['Timestamp']

0        2017-09-01 01:00:00
1        2017-09-01 01:01:00
2        2017-09-01 01:02:00
3        2017-09-01 01:03:00
4        2017-09-01 01:04:00
                 ...        
130975   2017-11-30 23:55:00
130976   2017-11-30 23:56:00
130977   2017-11-30 23:57:00
130978   2017-11-30 23:58:00
130979   2017-11-30 23:59:00
Name: Timestamp, Length: 130980, dtype: datetime64[ns]

## 3.CNN Model for time series prediction:


In [16]:
from keras.models import Sequential
from keras.layers import Dense
from keras.layers import LSTM
from sklearn.model_selection import train_test_split
from keras.models import Sequential
from keras.layers import LSTM, Dense, Dropout, Masking, Embedding
from keras.optimizers import SGD

In [23]:

y=df_final1['61']
x=df_final1.drop(columns=['Timestamp', '61'])



split=int(0.8*x.shape[0])
train=df_final1.iloc[:split,:]
test=df_final1.iloc[split:,:]

y_train=train['61']
X_train=train.drop(columns=['Timestamp', '61'])




m = Sequential()

m.add(Dense(25, kernel_initializer = 'uniform', activation = 'relu', input_dim = X_train.shape[1]))

m.add(Dense(100, activation = 'linear'))

m.add(Dense(1,activation='linear'))



m.compile(loss='mean_squared_error', optimizer='rmsprop', metrics=['mse'])



m.fit(X_train,y_train, epochs=50, batch_size=100)



Epoch 1/50
1048/1048 [==============================] - 1s 923us/step - loss: 149438.4844 - mse: 149438.4844 0s - loss: 201579.7031 - mse: 20
Epoch 2/50
1048/1048 [==============================] - 1s 931us/step - loss: 39619.1914 - mse: 39619.1914
Epoch 3/50
1048/1048 [==============================] - 1s 912us/step - loss: 28110.6074 - mse: 28110.6074
Epoch 4/50
1048/1048 [==============================] - 1s 860us/step - loss: 25355.0117 - mse: 25355.0117
Epoch 5/50
1048/1048 [==============================] - 1s 870us/step - loss: 23231.0527 - mse: 23231.0527
Epoch 6/50
1048/1048 [==============================] - 1s 879us/step - loss: 21374.3320 - mse: 21374.3320
Epoch 7/50
1048/1048 [==============================] - 1s 899us/step - loss: 19727.1836 - mse: 19727.1836
Epoch 8/50
1048/1048 [==============================] - 1s 893us/step - loss: 18088.8398 - mse: 18088.8398
Epoch 9/50
1048/1048 [==============================] - 1s 879us/step - loss: 16675.0312 - mse: 16675.0312
Ep

In [24]:
X_test=test.drop(columns=['Timestamp', '61'])
y_test=test['61'] ## original labels

In [25]:
predicted=m.predict(X_test)


In [26]:
predicted.flatten()

array([6173.6597, 6174.159 , 6177.023 , ..., 9879.715 , 9880.8   ,
       9882.607 ], dtype=float32)

In [27]:
predicted=predicted.reshape(test.shape[0],)

## 3.R2 score:

In [41]:
from sklearn.metrics import r2_score

In [42]:
r2_score(y_test, predicted)

0.9898874656640669

In [31]:
lst_pre=[]
for i in range(predicted.shape[0]):
    lst_pre.append(predicted[i]);



### 4. Actual v/s Predicted price

In [78]:


import plotly.graph_objs as go
from plotly.offline import *
import plotly

trace1 = go.Scatter(
    x=test['Timestamp'],
    y=lst_pre,
    mode = 'lines',
    name='Predicted'
)



trace2 = go.Scatter(
    x=test['Timestamp'],
    y=y_test,
    mode = 'lines',
    name='Closing Price'
)

data = [trace1, trace2]

layout = go.Layout(
    title='Number of Tweets'
)
fig = go.Figure(data=data, layout=layout)

fig.update_layout(
    showlegend = True,
    autosize=False,
    width=1000,
    height=950,
    margin=dict(
        l=50,
        r=50,
        b=100,
        t=100,
        pad=4
    ),
    paper_bgcolor="LightSteelBlue",)

plotly.offline.iplot(fig, filename='No_Of_Tweets.html') # Plot No. of Tweets

